# TF-IDF Analysis

TF-IDF (term frequency-inverse document frequency) analysis is a statistical technique used in natural language processing and information retrieval to determine the importance of a word in a document or corpus. It is a way to measure how relevant a word is to a document in a collection of documents.

TF-IDF analysis assigns a weight to each word in a document based on how frequently it appears in the document (term frequency) and how rare it is in the entire corpus (inverse document frequency). The weight assigned to a word increases proportionally with its frequency in the document, but is offset by the rarity of the word in the corpus. This means that words that appear frequently in a document but also appear frequently in many other documents in the corpus are given a lower weight, while words that appear less frequently in the corpus but frequently in a particular document are given a higher weight.

The output of TF-IDF analysis is a numerical representation of each document that captures the importance of each word in that document. This can be used for various tasks such as text classification, clustering, and information retrieval.

## Table of Contents
* [Connect to Database ](#Connect-to-database)
* [Import Datasets](#Import-Dataset)
* [Remove Stopwords](#Remove-stopwords)
* [Lemmatization](#Lemmatization)

In [1]:
#pip install mysql-connector-python
#!pip install wordcloud


## Connect to Database

In [2]:
import mysql.connector
import pandas as pd

#creds = ["username","password","juliehaegh","ninG20&19rea","3306"] 
creds = ["juliehaegh","ninG20&19rea","172.20.20.4","hgo",3306]

In [3]:
#Connection to the database
host = creds[2]
user = creds[0]
password = creds[1]
database = creds[3]
port = creds[4]
mydb = mysql.connector.connect(host=host, user=user, database=database, port=port, password=password, auth_plugin='mysql_native_password')
mycursor = mydb.cursor()

#Safecheck to guarantee that the connection worked
mycursor.execute('SHOW TABLES;')
print(f"Tables: {mycursor.fetchall()}")
print(mydb.connection_id) #it'll give connection_id,if got connected

Tables: [('ConsultaUrgencia_doentespedidosconsultaNeurologia2012',), ('consultaneurologia2012',), ('consultaneurologia201216anon_true',), ('hgo_data_032023',)]
118


## Import Datasets

In [4]:
# Import Alert P1 dataset
SClinic = pd.read_sql("""SELECT * FROM ConsultaUrgencia_doentespedidosconsultaNeurologia2012""",mydb)

# Import SClinic
AlertP1 = pd.read_sql("""SELECT * FROM consultaneurologia201216anon_true""",mydb)

# Replace all NaN with 0
AlertP1 = AlertP1.fillna(0)

# Add result column
AlertP1['result'] = ['Accepted' if x in [0,14,25,20,53,8,12,12] else 'Refused' for x in AlertP1['COD_MOTIVO_RECUSA']]

/var/folders/s4/b954cnz56f51x2w2tygb_fvc0000gn/T/ipykernel_40653/676277896.py:2: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  SClinic = pd.read_sql("""SELECT * FROM ConsultaUrgencia_doentespedidosconsultaNeurologia2012""",mydb)
/var/folders/s4/b954cnz56f51x2w2tygb_fvc0000gn/T/ipykernel_40653/676277896.py:5: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  AlertP1 = pd.read_sql("""SELECT * FROM consultaneurologia201216anon_true""",mydb)


In [5]:
# Create a new column with accepted and rejected cases
#SClinic['Accepted/Rejected'] = SClinic['COD_MOTIVO_RECUSA'].apply(lambda x: 'Accepted' if x == 0 else 'Rejected')
#SClinic = SClinic[(SClinic['Texto']!='') & (SClinic['Accepted/Rejected']=='Accepted')].iloc[887:987]
#SClinic = SClinic[SClinic['Texto']!='']
#SClinic

In [6]:
import math

# Split data into train and test
AlertP1_sorted = AlertP1[AlertP1['Texto']!=''].sort_values(by='DATA_RECEPCAO')

# calculate the index for the split
split_index = math.ceil(0.8 * len(AlertP1_sorted))

# split the data frame into test and train sets
train_set = AlertP1_sorted.iloc[:split_index]
test_set = AlertP1_sorted.iloc[split_index:]

In [7]:
# Import librariers 
import matplotlib.pyplot as plt
import numpy as np
from wordcloud import WordCloud, STOPWORDS
import nltk
nltk.download('stopwords')
nltk.download('punkt')
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from unidecode import unidecode
import re
from collections import Counter
import nltk
from nltk.corpus import stopwords
import warnings
warnings.filterwarnings(action="ignore")

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/juliehaegh/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/juliehaegh/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


## Remove Stopwords

In [8]:
# Get rid of special characters and transform Texto column to Latin words
train_set['Texto'] = train_set['Texto'].apply(lambda x: unidecode(x))

#The re.sub function is used to substitute all digits (\d) with an empty string
train_set['Texto'] = train_set['Texto'].apply(lambda x: re.sub(r'\d', '', x))

# Remove all names in Texto variable
# This function uses a regular expression to find all words in the text that start with a 
# capital letter (\b[A-Z][a-z]+\b), which are assumed to be names
text = train_set['Texto'] 

# remove all hyphens from the text
text = text.replace('-', '')

def remove_names(text):
    # Find all words that start with a capital letter
    names = re.findall(r'\b[A-Z][a-z]+\b', text)
    
    # Replace the names with an empty string
    for name in names:
        text = text.replace(name, '')
        
    return text

In [9]:
# Create an empty list to store the text
text_list = []

# Loop through the 'text' column
for text in text.str.lower(): # Transform every word to lower case
    text_list.append(text)

# Print the list of text
#print(text_list)

In [10]:
# Download the Portuguese stop words
nltk.download('stopwords')
nltk.download('punkt')

# Get the Portuguese stop words
stop_words = set(stopwords.words('portuguese'))

# Manually remove stopwords
stop_words.update(['-//','.', ',','(',')',':','-','?','+','/',';','2','1','drª','``','','3','desde','anos','doente','consulta','alterações','se',"''",'cerca','refere','hgo','utente','vossa','s','...','ainda','c','filha','costa','dr.','pereira','ja','--','p','dr','h','n','>','q','//','..','b','++','%','//','-','+++/','=','+++/'])

# Create a new list to store the filtered text
filtered_text = []

# Loop through the text_list and remove the stop words
for text in text_list:
    words = word_tokenize(text)
    words = [word for word in words if word.lower() not in stop_words]
    filtered_text.append(" ".join(words))

# Print the filtered text
#print(filtered_text)

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/juliehaegh/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/juliehaegh/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [11]:
# Save the filtered text as a new column to the dataframe
train_set['filtered_text'] = filtered_text

## Lemmatization

Lemmatization is a text normalization technique used in Natural Language Processing (NLP), that switches any kind of a word to its base root mode. Lemmatization is responsible for grouping different inflected forms of words into the root form, having the same meaning

In [12]:
# Define function for lemmatization
def spacy_lemmatizer(df):
    import spacy
    import pt_core_news_md
    nlp = pt_core_news_md.load()

    doclist = list(nlp.pipe(df))

    docs=[]
    for i, doc in enumerate(doclist):
        docs.append(' '.join([listitem.lemma_ for listitem in doc]))
        
    return docs

In [13]:
# create an empty list to store the words
word_list = []

# loop through each row of the "text_column" column
for index, row in train_set.iterrows():
    
    # split the text into individual words using whitespace as a delimiter
    words = row['filtered_text'].split()
    # add the words to the word list
    word_list.extend(words)

# print the word list
#print(word_list)

In [14]:
# create an empty list to store the words
word_list = []

# loop through each row of the "text_column" column
for index, row in train_set.iterrows():
    
    # split the text into individual words using whitespace as a delimiter
    words = row['filtered_text'].split()
    
    # remove hyphens from the words and add them to the word list
    word_list.extend([word.replace('-', '') for word in words])
    # remove slash from the words and ass them to the list
    word_list.extend([word.replace('/', '') for word in words])
    

# print the cleaned word list
#print(word_list)

In [15]:
Lemma = spacy_lemmatizer(word_list) # Call lemmatizer function

# print length of word_list and compare the count after doing lemmatization
from collections import Counter

items = Counter(Lemma).keys()
print('The number of words after lemmatization:',len(items))

items2 = Counter(word_list).keys()
print('The number of words before lemmatization:',len(items2))

The number of words after lemmatization: 8793
The number of words before lemmatization: 10712


In [16]:
# apply the spacy_lemmatizer function to each row in the 'text' column
train_set['text_lemmatized'] = spacy_lemmatizer(train_set['filtered_text'])

# drop rows with empty strings
train_set_filtered = train_set[['text_lemmatized','filtered_text','result']].replace('', pd.NA).dropna()
train_set_filtered = pd.DataFrame(train_set_filtered)
train_set_filtered

text_lemmatized  \
1540  dor lapso efoi-le dar alto qualquer justificac...   
525                                   relatorio clinico   
121   homem ap dm gamapatia monoclonal igm dca arter...   
168   mulher dor ponto lingua sensacao repuxamento l...   
1154                                          epilepsia   
...                                                 ...   
1619  justificacao optimizacao diagnosticar terapeut...   
902                                 referencia duplicar   
901                                 referencia duplicar   
1105  historia actual problema saude resolver parkin...   
624                                   relatorio clinico   

                                          filtered_text    result  
1540  dor lapso foi-lhe dada alta qualquer justifica...   Refused  
525                                   relatorio clinico   Refused  
121   homem ap dm gamapatia monoclonal igm dca arter...   Refused  
168   mulher dor ponta lingua sensacao repuxamento l...   Refused  
1154                                          epilepsia  Accepted  
...                                                 ...       ...  
1619  justificacao optimizacao diagnostica terapeuti...  Accepted  
902                                referencia duplicada   Refused  
901                                referencia duplicada  Accepted  
1105  historia actual problema saude resolver parkin...  Accepted  
624                                   relatorio clinico   Refused  

[1416 rows x 3 columns]

In [17]:
# Create a lambda function to apply to the DataFrame
train_set_filtered['accepted/rejected'] = train_set_filtered['result'].apply(lambda x: 1 if x == 'Accepted' else 0)

In [18]:
# Import Sklearn
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split

# Split the dataset into train and test sets with 20% test size
X_train, X_test, y_train, y_test = train_test_split(train_set_filtered['filtered_text'], train_set_filtered['accepted/rejected'], test_size=0.2, random_state=42)

# Create a TF-IDF vectorizer object with max_df = 0.8 and min_df = 5
tfidf_vectorizer = TfidfVectorizer(max_df=0.8, min_df=5)

# Fit and transform the training data into a sparse matrix of TF-IDF features
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)

# Transform the test data into a sparse matrix of TF-IDF features
X_test_tfidf = tfidf_vectorizer.transform(X_test)

# Use the TF scores for future predictions
tf_vectorizer = TfidfVectorizer(use_idf=False, max_df=0.8, min_df=5)
X_tf = tf_vectorizer.fit_transform(train_set_filtered['filtered_text'])

# Use the TF-IDF scores for logistic regression with other variables
X_train_tfidf_lr = pd.concat([pd.DataFrame(X_train_tfidf.toarray()), train_set_filtered[train_set_filtered.index.isin(X_train.index)].drop(['filtered_text', 'accepted/rejected'], axis=1)], axis=1)
X_test_tfidf_lr = pd.concat([pd.DataFrame(X_test_tfidf.toarray()), train_set_filtered[train_set_filtered.index.isin(X_test.index)].drop(['filtered_text', 'accepted/rejected'], axis=1)], axis=1)

max_df is a float in the range [0.0, 1.0] or an integer, representing the maximum frequency of a term allowed in the corpus. Terms with a frequency higher than this threshold will be ignored as they are considered too common to be informative. In the code provided, we set max_df=0.8, which means that we are ignoring terms that appear in more than 80% of the documents in the corpus.

min_df is also a float in the range [0.0, 1.0] or an integer, representing the minimum frequency of a term allowed in the corpus. Terms with a frequency lower than this threshold will be ignored as they are considered too rare to be informative. In the code provided, we set min_df=5, which means that we are ignoring terms that appear in less than 5 documents in the corpus

In [19]:
feature_names = tfidf_vectorizer.get_feature_names_out()
len(feature_names)

1738


# Test

In [20]:
# Split the data into train and test sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(train_set_filtered['filtered_text'], train_set_filtered['result'], test_size=0.2, random_state=42)

# Create the TF-IDF vectorizer object
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf_vectorizer = TfidfVectorizer(max_df=0.8, min_df=5)

# Fit and transform the vectorizer on the train set
X_train_tfidf = tfidf_vectorizer.fit_transform(X_train)

# Extract the top 10 words with the highest scores for the train set
train_scores = np.asarray(X_train_tfidf.mean(axis=0)).ravel().tolist()
train_features = tfidf_vectorizer.get_feature_names_out()
top_train_indices = np.argsort(train_scores)[::-1][:20]
top_train_words = [train_features[i] for i in top_train_indices]
top_train_scores = [train_scores[i] for i in top_train_indices]

# Transform the vectorizer on the test set
X_test_tfidf = tfidf_vectorizer.transform(X_test)

# Extract the top 10 words with the highest scores for the test set
test_scores = np.asarray(X_test_tfidf.mean(axis=0)).ravel().tolist()
test_features = tfidf_vectorizer.get_feature_names_out()
top_test_indices = np.argsort(test_scores)[::-1][:20]
top_test_words = [test_features[i] for i in top_test_indices]
top_test_scores = [test_scores[i] for i in top_test_indices]

# Print the results
print("Top 20 words with the highest scores for the train set:")
for word, score in zip(top_train_words, top_train_scores):
    print(f"{word}: {score:.4f}")

print("\nTop 20 words with the highest scores for the test set:")
for word, score in zip(top_test_words, top_test_scores):
    print(f"{word}: {score:.4f}")


Top 20 words with the highest scores for the train set:
relatorio: 0.0662
clinico: 0.0640
nao: 0.0308
epilepsia: 0.0282
ha: 0.0257
alteracoes: 0.0255
mg: 0.0237
neurologia: 0.0223
demencia: 0.0194
se: 0.0191
tremor: 0.0186
quadro: 0.0184
informacao: 0.0175
tac: 0.0172
memoria: 0.0169
ce: 0.0164
agravamento: 0.0162
dra: 0.0157
cefaleias: 0.0155
avaliacao: 0.0155

Top 20 words with the highest scores for the test set:
relatorio: 0.0588
clinico: 0.0554
epilepsia: 0.0350
alteracoes: 0.0350
nao: 0.0269
tremor: 0.0243
ha: 0.0240
informacao: 0.0228
memoria: 0.0227
neurologia: 0.0215
cefaleias: 0.0208
tac: 0.0207
demencia: 0.0200
ce: 0.0195
se: 0.0190
hta: 0.0176
parkinson: 0.0175
quadro: 0.0167
mg: 0.0160
cefaleia: 0.0155


In [21]:
#!pip install gensim

# Import modules
import gensim
from gensim.models import Word2Vec

# get the text data from a column in the DataFrame
text_data = train_set_filtered['text_lemmatized'].tolist()

# split the text data into sentences
sentences = [sentence.split() for sentence in text_data]

# train a Word2Vec model on the sentences
model = Word2Vec(sentences, min_count=1, vector_size=100, workers=4)

# get the Word2Vec vectors for the words in the vocabulary
vectors = model.wv.vectors

# get the vocabulary of the Word2Vec model
vocab = model.wv.key_to_index.keys()

# print the Word2Vec vectors and their corresponding words
for word, vector in zip(vocab, vectors):
    print(word, vector)

nao [-0.44132313  0.8565222   0.5686067  -0.0508663   0.22585852 -1.3588282
  0.56286013  1.8549955  -0.5995706  -0.58996016 -0.5823887  -1.4650999
 -0.18771157  0.12612899  0.08323921 -1.0262957   0.06412268 -1.3798444
  0.09185357 -1.6898232   0.40372586  0.5731307   0.513664   -0.312517
 -0.18691005  0.13915727 -0.67992055 -0.7771014  -1.286634    0.26832917
  0.83168834  0.2144268   0.35637817 -0.6024993  -0.12338693  1.2363776
  0.07036286 -0.83646005 -0.34305128 -1.986513   -0.04456438 -0.9692916
 -0.4418429  -0.1418655   0.9274336  -0.52176243 -0.5851305   0.03658699
  0.523806    0.6300863   0.52466094 -0.30297342 -0.1475002  -0.3083904
 -0.7336155   0.42516434  0.6884631  -0.01196092 -1.0406848   0.12518418
  0.26914078  0.42714518 -0.5219898  -0.0409603  -1.1898576   0.774331
  0.47204205  0.7631475  -1.3337231   1.3807933  -0.83809423  0.60626274
  0.94529974 -0.41856262  0.8973645   0.6187891   0.17565718 -0.00237878
 -0.7227729   0.18291263 -0.23852365 -0.13869813 -1.04790

olho [-0.07892243  0.14892465  0.10671403 -0.00401127  0.04569279 -0.23402053
  0.09245022  0.31005332 -0.1048007  -0.09121576 -0.09393636 -0.2531362
 -0.04124328  0.02718074  0.01230827 -0.17809065  0.01563852 -0.24260038
  0.0195338  -0.29271504  0.06509417  0.10186694  0.07810508 -0.05575786
 -0.0396191   0.02229096 -0.12664156 -0.13953471 -0.22875202  0.05115473
  0.15675616  0.03580027  0.04948236 -0.1108449  -0.03339437  0.21023794
  0.01246124 -0.14758238 -0.06388538 -0.35024682 -0.00735242 -0.17400813
 -0.06503055 -0.01397915  0.15502082 -0.095949   -0.09619242 -0.00674887
  0.09682685  0.10537975  0.08241531 -0.0607557  -0.03351111 -0.04376395
 -0.1264218   0.08132862  0.12489685 -0.0029135  -0.17253584  0.01398416
  0.05399355  0.06703337 -0.09765232 -0.00848051 -0.20842208  0.14118475
  0.08815763  0.13618228 -0.22139654  0.24087614 -0.14601782  0.11148366
  0.1639116  -0.07449288  0.14672096  0.10500835  0.0271436   0.00877944
 -0.12269127  0.03961363 -0.03457086 -0.0220045

compreensao [-0.03024461  0.04424575  0.02123289 -0.00125256  0.01688304 -0.06857306
  0.02855219  0.08130454 -0.02276091 -0.02473752 -0.02883932 -0.06270102
  0.00145899  0.00496414 -0.00110925 -0.05363226  0.0050455  -0.07300143
  0.01244325 -0.07825513  0.01979678  0.03010976  0.02573198 -0.01124965
 -0.00331582  0.01333712 -0.03055541 -0.03374963 -0.05487768  0.00412708
  0.03349118  0.00830254  0.02209529 -0.03199202 -0.01085511  0.05612981
  0.0026234  -0.04964526 -0.02709942 -0.09755771  0.00863688 -0.03851569
 -0.01972992 -0.01129854  0.05136167 -0.0295657  -0.02464684 -0.00395409
  0.03256147  0.02347144  0.01908825 -0.01000149 -0.00498559 -0.00949173
 -0.04387378  0.01550304  0.02426385  0.00885068 -0.05406247  0.00506673
  0.01328934  0.01415891 -0.03297385  0.0032448  -0.06259031  0.04861123
  0.02531882  0.04049347 -0.06203084  0.07173213 -0.03584508  0.02007058
  0.04131749 -0.02461701  0.04766452  0.03406213  0.00766678  0.00543997
 -0.0347228   0.0010736  -0.00321642  0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [26]:
# train a Word2Vec model on the sentences
model = Word2Vec(sentences, min_count=1, vector_size=100, workers=4)

# get the Word2Vec vectors for the words in the vocabulary
vectors = model.wv.vectors

# get the vocabulary of the Word2Vec model
vocab = model.wv.key_to_index.keys()

In [28]:
def sentence_to_features(sentence):
    features = []
    for word in sentence.split():
        try:
            features.append(model.wv[word])
        except KeyError:
            pass
    return np.mean(features, axis=0)

features = [sentence_to_features(sentence) for sentence in text_data]

In [30]:
features

[array([-0.06668171,  0.2078633 ,  0.09861877, -0.01112732,  0.06426959,
        -0.25394112,  0.04379584,  0.35315308, -0.10964145, -0.04717812,
        -0.15788366, -0.2928803 ,  0.02899455,  0.10274457,  0.02500469,
        -0.22689104,  0.02315548, -0.23306492, -0.0282742 , -0.3850724 ,
         0.07953059,  0.13622688,  0.05535262, -0.10685826, -0.05463197,
        -0.00577789, -0.1932877 , -0.16817537, -0.25684434,  0.00712814,
         0.21148188,  0.04995271,  0.06015458, -0.08921607, -0.07762717,
         0.3216637 ,  0.02538102, -0.20607539, -0.08281916, -0.4029034 ,
         0.04729344, -0.25748488, -0.08981957,  0.02865497,  0.17523965,
        -0.11224168, -0.19900446, -0.08416045,  0.06943378,  0.08808263,
         0.11791077, -0.11625439, -0.01880523, -0.05142828, -0.18165813,
         0.10517735,  0.13757814, -0.00224321, -0.2703149 ,  0.00245842,
         0.10339288,  0.05353656, -0.08813189, -0.06489121, -0.1974576 ,
         0.21171041,  0.06798834,  0.11458788, -0.2

# 

In [27]:
#NOT CORRECT

In [22]:
import pandas as pd
import numpy as np
from gensim.models import Word2Vec
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

# Load the text data from a column in the DataFrame
text_data = train_set_filtered['text_lemmatized'].tolist()

# Split the text data into sentences
sentences = [sentence.split() for sentence in text_data]

# Train a Word2Vec model on the sentences
model = Word2Vec(sentences, min_count=1, vector_size=100, workers=4)

# Define a function to generate features for a sentence
def sentence_to_features(sentence):
    features = []
    for word in sentence.split():
        try:
            features.append(model.wv[word])
        except KeyError:
            pass
    return np.mean(features, axis=0)

# Generate features for each sentence in the dataset
features = [sentence_to_features(sentence) for sentence in text_data]

# Split the dataset into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(features, train_set_filtered['filtered_text'], test_size=0.2, random_state=42)

# Train a logistic regression model on the training set
clf = LogisticRegression()
clf.fit(X_train, y_train)

# Make predictions on the testing set
y_pred = clf.predict(X_test)

# Evaluate the accuracy of the model
accuracy = accuracy_score(y_test, y_pred)
print(f'Accuracy: {accuracy}')

Accuracy: 0.13028169014084506


In [23]:
import gensim
from gensim.models import Word2Vec
from sklearn.feature_extraction.text import TfidfVectorizer

# get the text data from a column in the DataFrame
text_data = train_set_filtered['text_lemmatized'].tolist()

# create a TF-IDF vectorizer
tfidf = TfidfVectorizer()
tfidf.fit(text_data)

# transform the text data into a TF-IDF matrix
tfidf_matrix = tfidf.transform(text_data)

# train a Word2Vec model on the sentences
sentences = [sentence.split() for sentence in text_data]
model = Word2Vec(sentences, min_count=1, vector_size=100, workers=4)

# get the Word2Vec vectors for the words in the vocabulary
vectors = model.wv.vectors

# get the vocabulary of the Word2Vec model
vocab = model.wv.key_to_index.keys()

# compute the TF-IDF weighted Word2Vec vectors
weighted_vectors = []
for i, word in enumerate(vocab):
    tfidf_score = tfidf.idf_[tfidf.vocabulary_[word]] if word in tfidf.vocabulary_ else 1
    weighted_vector = vectors[i] * tfidf_score
    weighted_vectors.append(weighted_vector)

# print the weighted Word2Vec vectors and their corresponding words
for word, vector in zip(vocab, weighted_vectors):
    print(word, vector)

nao [-1.1794231   1.8942738   0.83339626 -0.2454209   0.4964279  -3.1599088
  1.2133962   4.2224784  -1.5536213  -1.0631186  -1.5310981  -3.5678177
 -0.3008991   0.42935297  0.5176279  -2.2489412   0.3120661  -2.9796815
 -0.01956123 -3.9955995   1.1573428   1.2148582   1.2116629  -0.6757191
 -0.3787564   0.24252214 -1.4513628  -1.6354935  -2.8654325   0.21705505
  1.9298201   0.3849485   1.1296355  -1.3640141  -0.33254033  2.8560932
  0.30290365 -2.1389408  -0.8524645  -4.4780955  -0.02718584 -2.1891966
 -0.95420134 -0.4141065   2.0145235  -1.282381   -1.4738369   0.06656942
  1.1535153   1.4051322   1.228314   -0.6992784  -0.4489824  -0.7437084
 -1.6547527   1.0232884   1.4239426  -0.05605909 -2.4919498   0.49288356
  0.5373279   0.95417565 -1.0272293  -0.43261245 -2.8217933   1.876179
  1.027548    1.9664087  -3.2624588   2.9962723  -1.7765077   1.4090679
  2.0781207  -1.3380336   2.1648958   1.5174356   0.5140949   0.138289
 -1.6308879   0.66960514 -0.51567113 -0.42665225 -2.154585 

paralisia [-0.18344331  0.4552079   0.10136103 -0.06174259  0.16117188 -0.6713704
  0.12305529  0.90918654 -0.3304008  -0.15762031 -0.47352967 -0.72519606
 -0.01854478  0.20788965  0.14543453 -0.5135798   0.03813663 -0.5126292
 -0.05917336 -0.86344963  0.23882681  0.32247537  0.14343701 -0.282303
 -0.02624233 -0.09118929 -0.37443584 -0.46081477 -0.60438424  0.05337745
  0.4592716   0.12524173  0.27542534 -0.21398473 -0.13542637  0.7385069
  0.00174539 -0.4890081  -0.11989189 -0.95481646  0.08650954 -0.59825486
 -0.15283221 -0.03673832  0.36202335 -0.24056    -0.3793957  -0.09388648
  0.18096703  0.14077528  0.33073506 -0.28382492 -0.15093516 -0.135847
 -0.45601246  0.2116361   0.35144368  0.02958592 -0.6445018   0.05639811
  0.2900394   0.28442127 -0.29321906 -0.20743737 -0.555422    0.4521829
  0.18287858  0.27380496 -0.71698546  0.58545536 -0.50098354  0.2388164
  0.34732217 -0.36688617  0.6172891   0.27311748  0.10696945  0.13145687
 -0.38230234  0.20997484 -0.14421375 -0.12153466 -

raquel [-0.13771805  0.27451304  0.14911139 -0.00685667  0.07385123 -0.44520947
  0.15926419  0.6239246  -0.16120866 -0.07545027 -0.2661603  -0.49423888
 -0.04577456  0.15005486  0.05828497 -0.31049207  0.09003591 -0.36485687
 -0.0322911  -0.5356812   0.13472417  0.23458469  0.11233933 -0.1410717
 -0.01068859  0.05144425 -0.29784536 -0.27071068 -0.46185052  0.08423078
  0.32194576  0.00987289  0.13209668 -0.15570894 -0.04357421  0.45648515
  0.04838791 -0.36389562 -0.13047539 -0.6481096   0.08069362 -0.32255524
 -0.14005995  0.01467707  0.22935045 -0.22496493 -0.29463357 -0.12956788
  0.13832179  0.12472259  0.22031176 -0.13810264 -0.0311469  -0.05162332
 -0.24247798  0.143462    0.17188752 -0.02027541 -0.3995221   0.0611859
  0.14680906  0.17493851 -0.13692877 -0.09923183 -0.35645524  0.34310418
  0.10348901  0.2406896  -0.47605613  0.33833724 -0.27733943  0.14490402
  0.2525139  -0.17179285  0.33684304  0.20146224  0.03175678  0.06647498
 -0.19987993  0.07039442 -0.06434282 -0.098375

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

